# **ERA5 Animation**

#### This notebook gives the script for making animation of any variable from ERA5 data.
#### Here, precipitation is the subject variable

In [14]:
import matplotlib.pyplot as plt
import imageio
import numpy as np
import pandas as pd
import os
import cmaps as cm
import geopandas as gp
from cartopy.mpl.gridliner import LATITUDE_FORMATTER, LONGITUDE_FORMATTER
import matplotlib.ticker as mticker
import matplotlib.animation as animation
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import xarray as xr

#### Define paths and certain variables. 

In [15]:
df_country="path_to_country_shapefile"
df_state="path_to_state_shapefile"
path = "path_to input_file_directory"
data = "era5_tp_hourly_JJAS2025.nc"
out_dir = "path_to_output_directory"
start_date = "2025-08-23T00"
end_date = "2025-08-27T00"


In [16]:
def era5_hourly_animation(
    filename,
    start_date,
    end_date,
    state_path,
    country_path,
    variable='tp',
    rename_dims={'latitude': 'lat', 'longitude': 'lon', 'valid_time': 'time'},
    cmap = cm.MPL_terrain_r,
    levels=np.concatenate(( np.array([1]),  np.arange(2, 30, 2))),
    extent=[71.5, 82.5, 26, 37],
    interval=250  # interval between frames in ms
):
    ds = xr.open_dataset(filename)
    ds = ds.rename(rename_dims)
    da = ds[variable].sel(time=slice(start_date, end_date)) * 1000  # scale if needed

    df_country = gp.read_file(country_path).to_crs(ccrs.PlateCarree())
    df_state = gp.read_file(state_path).to_crs(ccrs.PlateCarree())

    fig, ax = plt.subplots(figsize=(8, 5), subplot_kw=dict(projection=ccrs.PlateCarree()))
    ax.set_extent(extent, crs=ccrs.PlateCarree())
    im = None

    def init():
        frame = da.isel(time=0)
        nonlocal im
        im = frame.plot(ax=ax, cmap=cmap, levels=levels, add_colorbar=True, extend='both')
        ax.coastlines()
        ax.add_geometries(df_country.geometry, edgecolor='k', facecolor='none', linewidth=1, crs=ccrs.PlateCarree())
        ax.add_geometries(df_state.geometry, edgecolor='k', facecolor='none', linewidth=0.3, crs=ccrs.PlateCarree())
        gl = ax.gridlines(draw_labels=True, alpha=0.3)
        gl.right_labels = False
        gl.top_labels = False
        gl.xformatter = LONGITUDE_FORMATTER
        gl.yformatter = LATITUDE_FORMATTER
        gl.xlocator = mticker.MultipleLocator(3)
        gl.ylocator = mticker.MultipleLocator(2)
        ax.set_title(pd.to_datetime(str(frame.time.values)).strftime(f"{variable} %Y-%m-%d %H:%M"))
        return im,

    def update(frame):
        data = da.isel(time=frame)
        im.set_array(data.values)  # Use 2D array directly, do not flatten
        ax.set_title(pd.to_datetime(str(data.time.values)).strftime(f"{variable} %Y-%m-%d %H:%M"))
        return im,


    ani = animation.FuncAnimation(fig, update, frames=da.sizes['time'], init_func=init, interval=interval, blit=False)
    plt.close(fig)
    return ani


In [17]:
from IPython.display import HTML
ani = era5_hourly_animation(
    filename=path+data,
    start_date=start_date,
    end_date=end_date,
    state_path=df_state,
    country_path=df_country,
    variable='tp',
    cmap=cm.MPL_terrain_r,
)
HTML(ani.to_jshtml())

